In [4]:
import os
import re
from collections import defaultdict
import pickle
from multiprocessing import Pool
from multiprocessing.dummy import Pool as ThreadPool

import chess
from chess.pgn import read_game

import numpy as np

In [5]:
def extract_moves(game):
    # Takes a game from the pgn and creates list of the board state and the next
    # move that was made from that position.  The next move will be our 
    # prediction target when we turn this data over to the ConvNN.
    positions = list()
    board = chess.Board()
    moves = list(game.main_line())
    for move in moves:
        position, move_code = board.fen(), move.uci()
        positions.append([position, move_code])
        board.push(move)     
    return positions

def replace_nums(line):
    # This function cycles through a string which represents one line on the
    # chess board from the FEN notation.  It will then swap out the numbers
    # for an equivalent number of spaces.
    return ''.join([' '*8 if h=='8' else ' '*int(h) if h.isdigit() else'\n'if h=='/'else ''+h for h in line])
    
def split_fen(fen):
    # Takes the fen string and splits it into its component lines corresponding
    # to lines on the chess board and the game status. 
    fen_comps = fen.split(' ', maxsplit = 1)
    board = fen_comps[0].split('/')
    status = fen_comps[1]
    board = [replace_nums(line) for line in board]
    return board, status

def list_to_matrix(board_list):
    # Converts a list of strings into a numpy array by first 
    # converting each string into a list of its characters. 
    pos_list = [list(line) for line in board_list]
    return np.array(pos_list)

def channelize(mat):
    # processes a board into a 8 x 8 x 6 matrix where there is a 
    # channel for each type of piece.  1's correspond to white, and 
    # -1's correpond to black.
    output = np.empty([8, 8, 6])
    wpcs = ['P', 'R', 'N', 'B', 'Q', 'K']
    bpcs = ['p', 'r', 'n', 'b', 'q', 'k']
    positions = [np.isin(mat, pc).astype('int') - np.isin(mat, bpcs[i]).astype('int') for i, pc in enumerate(wpcs)]
    return np.stack(positions)

def process_status(status):
    # The last combination of characters in the FEN notation convey some different pieces of information
    # like the player who is to move next, and who can still castle. 
    # I have written the code to extract all of the different pieces, but the Agent will only need to know next_to_move. 
    splt = status.split(" ")
    next_to_move = splt[0]
    castling = splt[1]
    en_passant = splt[2]
    half_clock = splt[3]
    full_clock = splt[4]
    return next_to_move

def process_game(game):
    # Takes a single game from a pgn and produces a dict of dicts which contains 
    # the board state, the next player to move, and the what the next move was (the prediction task).
    positions = extract_moves(game)
    boards = []
    next_to_move = []
    for position in positions:
        board, status = split_fen(position[0])
        boards.append(channelize(list_to_matrix(board)))
        
        pos_dict[str(game.__hash__()) + str(i)]['next_to_move'] = process_status(status), position[1]
        pos_dict[str(game.__hash__()) + str(i)]['target'] = 
    return pos_dict

def write_game_to_file(game_dict, filename):
    # Takes a dictionary and a filename and saves a pickle file to disk
    pickle.dump(game_dict, open("".join(['data/', filename, '.p']), "wb"))
    
def read_and_process(iteration):
    gm = read_game(pgn)
    game = process_game(gm)
    print("".join(["Completed: ", str(iteration),]))
    return game

def wrangle_data(num_games=10000, save_file=False, filename="chess matrices"):
    pool = ThreadPool(12)
    results = pool.map(read_and_process, range(num_games))
    pool.close() 
    pool.join()
    results = { k: v for d in results for k, v in d.items() }
    if save_file:
        write_game_to_file(results, filename)
    return results

In [6]:
with open('data/KingBase2017-A00-A39.pgn', encoding='latin-1') as pgn:
    results = wrangle_data()

error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'xa1' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Nb6' in rnbqkbnr/pppppppp/8/8/7P/8/PPPPPPP1/RNBQKBNR b KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bay

error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Qb1' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Rb5' in rnbqkbnr/pppppppp/8/8/1P6/8/P1PPPPPP/RNBQKBNR b KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\ba

error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Nxf6' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Qe7' in rnbqkbnr/ppppppp1/8/7p/7P/8/PPPPPPP1/RNBQKBNR w KQkq - 0 2
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\b

error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Kc2' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Rc2' in rnbqkbnr/pppppppp/8/8/1P6/8/P1PPPPPP/RNBQKBNR b KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\ba

Completed: 0
Completed: 2090
Completed: 2299
Completed: 2300


...

Completed: 9745
Completed: 8535
Completed: 8736
Completed: 9566Completed: 8536

Completed: 7933


error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Rf1' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Kf6' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1
error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\baye

Completed: 9155
Completed: 8957
Completed: 9358
Completed: 9567


error during pgn parsing
Traceback (most recent call last):
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\pgn.py", line 936, in read_game
    move = board_stack[-1].parse_san(token)
  File "C:\Anaconda3\envs\bayes\lib\site-packages\chess\__init__.py", line 2737, in parse_san
    raise ValueError("illegal san: {0} in {1}".format(repr(san), self.fen()))
ValueError: illegal san: 'Kc3' in rnbqkbnr/pppppppp/8/8/8/8/PPPPPPPP/RNBQKBNR w KQkq - 0 1


Completed: 9156Completed: 9746Completed: 9963


Completed: 8537
Completed: 8116
Completed: 8319
Completed: 9964
Completed: 8117
Completed: 7934
Completed: 9965
Completed: 8737
Completed: 9359
Completed: 8958
Completed: 9157
Completed: 8959
Completed: 9568
Completed: 9747
Completed: 7935
Completed: 8118
Completed: 8538
Completed: 8960
Completed: 8320
Completed: 9966
Completed: 8738
Completed: 7936
Completed: 8961
Completed: 9360
Completed: 9748
Completed: 9158
Completed: 9361
Completed: 9569
Completed: 8119
Completed: 8321
Completed: 8739
Completed: 9159
Completed: 9967
Completed: 8539
Completed: 7937
Completed: 8740
Completed: 8120
Completed: 8962
Completed: 7938
Completed: 9362Completed: 9749

Completed: 8322
Completed: 9160
Completed: 9750
Completed: 9570Completed: 8540

Completed: 8121
Completed: 7939
Completed: 8963
Completed: 7940
Completed: 9968Completed: 9161

Completed: 8741
Completed: 8122
Completed: 9969
Completed: 9751
Completed: 9363
Completed: 9571
Completed: 8964
Complete

In [7]:
results

{'893720765410': {'board_state': array([[[ 0,  0,  0,  0,  0,  0,  0,  0],
          [-1, -1, -1, -1, -1, -1, -1, -1],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 1,  1,  1,  1,  1,  1,  1,  1],
          [ 0,  0,  0,  0,  0,  0,  0,  0]],
  
         [[-1,  0,  0,  0,  0,  0,  0, -1],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 1,  0,  0,  0,  0,  0,  0,  1]],
  
         [[ 0, -1,  0,  0,  0,  0, -1,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0,  0],
          [ 0,  0,  0,  0,  0,  0,  0